In [25]:
import onnxruntime
import torch
from PIL import Image
import cv2
import torchvision.transforms as transforms
import numpy as np


In [26]:
handwrite_mean=(0.877, 0.877, 0.877)
handwrite_std=(0.200, 0.200, 0.200)

# 减少图像白边
def cutImg(img):
    dst = 255- img
    gray = cv2.cvtColor(dst,cv2.COLOR_BGR2GRAY)  
    ret, binary = cv2.threshold(gray,127,255,cv2.THRESH_BINARY)  
    
    contours, hierarchy = cv2.findContours(binary,cv2.RETR_TREE,cv2.CHAIN_APPROX_SIMPLE)

    minx = 65523
    miny = 65523
    maxx = 0
    maxy = 0

    for contour in contours:
        boundRect = cv2.boundingRect(contour)
        (x,y,w,h)=boundRect
        if x<minx:
            minx=x
        if y<miny:
            miny=y
        if x+w>maxx:
            maxx=x+w
        if y+h>maxy:
            maxy=y+h
    cutw=maxx-minx
    cuth=maxy-miny
    # w>h
    # if cutw>cuth:
    #     cuty1=int((maxy+miny)/2-cutw/2)
    #     cuty2=int((maxy+miny)/2+cutw/2)
    #     img = img[cuty1:cuty2,minx:maxx]
    # if cutw<cuth:
    #     cutx1=int((maxx+minx)/2-cuth/2)
    #     cutx2=int((maxx+minx)/2+cuth/2)
    #     img = img[miny:maxy,cutx1:cutx2] 
    img = img[miny:maxy,minx:maxx]
    return img

def to_numpy(tensor):
    return tensor.detach().cpu().numpy() if tensor.requires_grad else tensor.cpu().numpy()
    
test = 'data/test/receive.png'

In [27]:
img = cv2.imread(test)
img = cutImg(img)
image = Image.fromarray(cv2.cvtColor(img,cv2.COLOR_BGR2RGB))
# cv2.imwrite('dealcut.png',img)
# image = Image.open(test).convert('RGB')

transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean = handwrite_mean, std = handwrite_std)
])
img_tensor = transform(image).unsqueeze(0)


In [28]:
ort_session = onnxruntime.InferenceSession('onnx/handwriting.onnx')
ort_inputs = {ort_session.get_inputs()[0].name: to_numpy(img_tensor)}


In [29]:
ort_outs = ort_session.run(None, ort_inputs)
print(ort_outs)

[array([[-63.502773, -50.50067 , -58.770657, ..., -60.615524, -62.879475,
        -58.971222]], dtype=float32)]


In [30]:
ret = np.array(ort_outs[0][0])
result = np.argsort(-ret)
print(result)

[3594 2715 1533 ... 3279 1428 1398]
